[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/meta-llama/llama-stack/blob/main/docs/notebooks/Alpha_Llama_Stack_Post_Training.ipynb)

# [Alpha] Llama Stack Post Training
This notebook will use a real world problem (improve LLM as tax preparer) to walk through the main sets of APIs we offer with Llama stack for post training to improve the LLM performance for agentic apps (We support supervised finetune now, RLHF and knowledge distillation will come soon!).

We will also showcase how to leverage existing Llama stack [inference APIs](https://github.com/meta-llama/llama-stack/blob/main/llama_stack/apis/inference/inference.py) (ollama as provider) to get the new model's output and the [eval APIs](https://github.com/meta-llama/llama-stack/blob/main/llama_stack/apis/eval/eval.py) to help you better measure the new model performance. We hope the flywheel of post-training -> eval -> inference can greatly empower agentic apps development.


- Read more about Llama Stack: https://llama-stack.readthedocs.io/en/latest/introduction/index.html
- Read more about post training APIs definition: https://github.com/meta-llama/llama-stack/blob/main/llama_stack/apis/post_training/post_training.py


Resource requirement:
- You can run this notebook with Llama 3.2 3B instruct model on Colab's **FREE** T4 GPU
- You can run this notebook with Llama 3.1 8B instruct model on Colab's A100 GPU or any GPU types with more than 22GB memory
- You need to spin up an ollama server on local host (will provider step by step instruction on this)

> **Note**: Llama Stack post training APIs are in alpha release stage and still under heavy development


# 0. Bootstrapping Llama Stack Library
In order to run post training on the Llama models, you will need to use a post training providers. Currently, the post training APIs are powered by **torchtune** as provider.

To learn more about torchtune: https://github.com/pytorch/torchtune

We will use [experimental-post-training](https://github.com/meta-llama/llama-stack/tree/main/llama_stack/templates/experimental-post-training) as the distribution template

####  0.0. Prerequisite: Have an OpenAI API key
In this showcase, we will use [braintrust](https://www.braintrust.dev/) as scoring provider for eval and it uses OpenAI model as judge model for scoring. So, you need to get an API key from [OpenAI developer platform](https://platform.openai.com/docs/overview).


> **Note:**
- Set the API Key in the Secrets of this notebook as `OPENAI_API_KEY`

You can choose from the list of [scoring providers](https://github.com/meta-llama/llama-stack/tree/main/llama_stack/providers/inline/scoring) and scoring functions that fulfill your need.



In [ ]:
!pip install git+https://github.com/meta-llama/llama-stack.git #TODO: update this after the next pkg release

  Cloning https://github.com/meta-llama/llama-stack.git (to revision hf_format_checkpointer) to /tmp/pip-req-build-j_1bxqzm
  Running command git clone --filter=blob:none --quiet https://github.com/meta-llama/llama-stack.git /tmp/pip-req-build-j_1bxqzm
  Running command git checkout -b hf_format_checkpointer --track origin/hf_format_checkpointer
  Switched to a new branch 'hf_format_checkpointer'
  Branch 'hf_format_checkpointer' set up to track remote branch 'hf_format_checkpointer' from 'origin'.
  Resolved https://github.com/meta-llama/llama-stack.git to commit 0fb674d77bb1a84d4e2dc9825102849ea06ba17b
  Running command git submodule update --init --recursive -q


In [ ]:
!llama stack build --template experimental-post-training --image-type venv --image-name __system__

Installing dependencies in system Python environment
Using Python 3.11.11 environment at: /usr
Audited 1 package in 176ms
Installing pip dependencies
Using Python 3.11.11 environment at: /usr
Resolved 130 packages in 1.82s
   Building fairscale==0.4.13
   Building fairscale==0.4.13
   Building antlr4-python3-runtime==4.9.3
   Building fairscale==0.4.13
   Building antlr4-python3-runtime==4.9.3
   Building zmq==0.0.0
   Building fairscale==0.4.13
   Building antlr4-python3-runtime==4.9.3
   Building zmq==0.0.0
⠙ Preparing packages... (0/46)
   Building fairscale==0.4.13
   Building antlr4-python3-runtime==4.9.3
   Building zmq==0.0.0
⠙ Preparing packages... (0/46)
   Building fairscale==0.4.13
   Building antlr4-python3-runtime==4.9.3
   Building zmq==0.0.0
⠙ Preparing packages... (0/46)
importlib-metadata ------------------------------     0 B/25.89 KiB
   Building fairscale==0.4.13
   Building antlr4-python3-runtime==4.9.3
   Building zmq==0.0.0
⠙ Preparing packages... (0/46)
importli

#### 0.1. spin up ollama server

We need to spin up an [ollama](https://github.com/ollama/ollama) server on local host to run the inference and eval

First we install xterm so that we can run command line tools

In [ ]:
!pip install uv colab-xterm
%load_ext colabxterm

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.2/16.2 MB 107.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.6/115.6 kB 12.2 MB/s eta 0:00:00


In [ ]:
!curl https://ollama.ai/install.sh | sh

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 13269    0 13269    0     0  37986      0 --:--:-- --:--:-- --:--:-- 38020
>>> Installing ollama to /usr/local
>>> Downloading Linux amd64 bundle
############################################################################################# 100.0%
>>> Creating ollama user...
>>> Adding ollama user to video group...
>>> Adding current user to ollama group...
>>> Creating ollama systemd service...
>>> The Ollama API is now available at 127.0.0.1:11434.
>>> Install complete. Run "ollama" from the command line.


Next, run xterm to run ollama as an independent process that stays alive. We choose Llama3.2 3B Instruct model for our tax preparation task, so we need to run llama3.2 3b instruct model on ollama


```
ollama serve &
ollama run llama3.2:3b --keepalive 120m
```

In [ ]:
%xterm

# ollama serve &
# ollama run llama3.2:3b --keepalive 120m

Launching Xterm...

<IPython.core.display.Javascript object>

Check which model is running on ollama

In [ ]:
!ollama ps

NAME           ID              SIZE      PROCESSOR    UNTIL            
llama3.2:3b    a80c4f17acd5    4.0 GB    100% GPU     2 hours from now    


In [ ]:
!pip install pypdf

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 300.7/300.7 kB 19.8 MB/s eta 0:00:00


Start the llama stack server

In [ ]:
import os
from google.colab import userdata

os.environ['OPENAI_API_KEY'] = userdata.get('OPENAI_API_KEY')

from llama_stack.distribution.library_client import LlamaStackAsLibraryClient
client = LlamaStackAsLibraryClient("experimental-post-training")
_ = client.initialize()

INFO:datasets:PyTorch version 2.5.1+cu124 available.
INFO:datasets:Polars version 1.9.0 available.
INFO:datasets:Duckdb version 1.1.3 available.
INFO:datasets:TensorFlow version 2.18.0 available.
INFO:datasets:JAX version 0.4.33 available.
INFO:llama_stack.distribution.stack:Scoring_fns: basic::equality served by basic
INFO:llama_stack.distribution.stack:Scoring_fns: basic::subset_of served by basic
INFO:llama_stack.distribution.stack:Scoring_fns: basic::regex_parser_multiple_choice_answer served by basic
INFO:llama_stack.distribution.stack:Scoring_fns: braintrust::factuality served by braintrust
INFO:llama_stack.distribution.stack:Scoring_fns: braintrust::answer-correctness served by braintrust
INFO:llama_stack.distribution.stack:Scoring_fns: braintrust::answer-relevancy served by braintrust
INFO:llama_stack.distribution.stack:Scoring_fns: braintrust::answer-similarity served by braintrust
INFO:llama_stack.distribution.stack:Scoring_fns: braintrust::faithfulness served by braintrust
I

Using config experimental-post-training:

apis:
- agents
- datasetio
- eval
- inference
- vector_io
- safety
- scoring
- telemetry
- post_training
- tool_runtime
benchmarks: []
container_image: null
datasets: []
image_name: experimental-post-training
metadata_store:
  db_path: /root/.llama/distributions/meta-reference-gpu/registry.db
  namespace: null
  type: sqlite
models: []
providers:
  agents:
  - config:
      persistence_store:
        db_path: /root/.llama/distributions/meta-reference-gpu/agents_store.db
        namespace: null
        type: sqlite
    provider_id: meta-reference
    provider_type: inline::meta-reference
  datasetio:
  - config: {}
    provider_id: localfs
    provider_type: inline::localfs
  eval:
  - config: {}
    provider_id: meta-reference
    provider_type: inline::meta-reference
  inference:
  - config:
      checkpoint_dir: null
      create_distributed_process_group: false
      max_seq_len: 4096
    provider_id: meta-reference-inference
    provider_type: inline::meta-reference
  - config:
      url: http://localhost:11434
    provider_id: ollama
    provider_type: remote::ollama
  post_training:
  - config:
      checkpoint_format: huggingface
    provider_id: torchtune-post-training
    provider_type: inline::torchtune
  safety:
  - config: {}
    provider_id: llama-guard
    provider_type: inline::llama-guard
  scoring:
  - config: {}
    provider_id: basic
    provider_type: inline::basic
  - config:
      openai_api_key: '********'
    provider_id: braintrust
    provider_type: inline::braintrust
  telemetry:
  - config: {}
    provider_id: meta-reference
    provider_type: inline::meta-reference
  tool_runtime:
  - config:
      api_key: '********'
      max_results: 3
    provider_id: brave-search
    provider_type: remote::brave-search
  vector_io:
  - config:
      kvstore:
        db_path: /root/.llama/distributions/meta-reference-gpu/faiss_store.db
        namespace: null
        type: sqlite
    provider_id: faiss
    provider_type: inline::faiss
scoring_fns: []
server:
  port: 8321
  tls_certfile: null
  tls_keyfile: null
shields: []
tool_groups: []
vector_dbs: []
version: '2'

## 1. Eval the native Llama model
First of all, we'd like to measure the native Llama 3.2 3B instruct model performance as a tax preparer.

#### 1.0. Prepare the eval dataset

We prepared a synthetic tax Q&A dataset from Llama 3.3 70B model [tax_preparation_eval.csv](https://gist.github.com/SLR722/0420c558ec681b00ed05fa1171505a38) (data source: https://github.com/shadi-fsai/modeluniversity/blob/main/test_questions.json).

- You can create your own eval dataset that repects Llama stack [eval dataset format](https://github.com/meta-llama/llama-stack/blob/91907b714e825a1bfbca5271e0f403aab5f10752/llama_stack/providers/utils/common/data_schema_validator.py#L43)



In [ ]:
import requests

# Upload the example dataset from github to notebook
url = 'https://gist.githubusercontent.com/SLR722/0420c558ec681b00ed05fa1171505a38/raw/dbc7ab86e71e808c4bae50b68b8bff60c1d239a5/tax_preparation_eval.csv'
r = requests.get(url)
with open('tax_preparation_eval.csv', 'wb') as f:
    f.write(r.content)

# You can use the below comment out code to upload your local file to the notebook
# from google.colab import files

# uploaded = files.upload()

In [ ]:
import mimetypes
import base64

# encode the dataset file into data_url
def data_url_from_file(file_path: str) -> str:
    if not os.path.exists(file_path):
        raise FileNotFoundError(f"File not found: {file_path}")

    with open(file_path, "rb") as file:
        file_content = file.read()

    base64_content = base64.b64encode(file_content).decode("utf-8")
    mime_type, _ = mimetypes.guess_type(file_path)

    data_url = f"data:{mime_type};base64,{base64_content}"

    return data_url

data_url = data_url_from_file("tax_preparation_eval.csv")

# register the eval dataset
response = client.datasets.register(
    purpose="eval/messages-answer",
    source={
        "type": "uri",
        "uri": data_url,
    },
    dataset_id="eval_dataset",
)

00:30:00.325 [START] /v1/datasets


#### 1.1. Register the eval model candidate with [models APIs](https://github.com/meta-llama/llama-stack/blob/e3f187fb83f2c45d5f838663658a873fb0fcc6d9/llama_stack/apis/models/models.py)
Since we use ollama as provider for inference, we set provider_id to 'ollama' during model registration


In [ ]:
from rich.pretty import pprint

response = client.models.register(
    model_id="meta-llama/Llama-3.2-3B-Instruct",
    provider_id="ollama",
    provider_model_id="llama3.2:3b",
    # base model id
    metadata={"llama_model": "meta-llama/Llama-3.2-3B-Instruct"},
)

pprint(response)

INFO:httpx:HTTP Request: GET http://localhost:11434/api/ps "HTTP/1.1 200 OK"


00:30:29.540 [START] /v1/models


Model(
│   identifier='meta-llama/Llama-3.2-3B-Instruct',
│   metadata={'llama_model': 'meta-llama/Llama-3.2-3B-Instruct'},
│   api_model_type='llm',
│   provider_id='ollama',
│   provider_resource_id='llama3.2:3b',
│   type='model',
│   model_type='llm'
)

#### 1.2. Kick-off eval job
- More details on Llama-stack eval: https://llama-stack.readthedocs.io/en/latest/benchmark_evaluations/index.html
  - Define an EvalCandidate
  - Run evaluate on datasets (we choose brainstrust's answer-similarity as scoring function with OpenAI's model as judge model)

  > **Note**: If the eval process is stuck, try to restart the ollama server and try again




In [ ]:
eval_rows = client.datasetio.get_rows_paginated(
    dataset_id="eval_dataset",
    limit=-1,
)

from tqdm import tqdm

client.benchmarks.register(
    benchmark_id="llama3.2-3B-instruct:tax_eval",
    dataset_id="eval_dataset",
    scoring_functions=["braintrust::answer-similarity"]
)

response = client.eval.evaluate_rows(
    benchmark_id="llama3.2-3B-instruct:tax_eval",
    input_rows=eval_rows.data,
    scoring_functions=["braintrust::answer-similarity"],
    benchmark_config={
        "type": "benchmark",
        "eval_candidate": {
            "type": "model",
            "model": "meta-llama/Llama-3.2-3B-Instruct",
            "sampling_params": {
                "temperature": 0.0,
                "max_tokens": 4096,
                "top_p": 0.9,
                "repeat_penalty": 1.0,
            },
        }
    }
)
pprint(response)

00:35:56.357 [START] /v1/datasetio/rows
00:35:56.357 [END] /v1/datasetio/rows [StatusCode.OK] (0.31ms)
00:35:56.369 [START] /v1/eval/benchmarks


  0%|          | 0/43 [00:00<?, ?it/s]

00:35:56.378 [END] /v1/eval/benchmarks [StatusCode.OK] (8.48ms)
00:35:56.397 [START] /v1/eval/benchmarks/llama3.2-3B-instruct:tax_eval/evaluations


INFO:httpx:HTTP Request: POST http://localhost:11434/api/generate "HTTP/1.1 200 OK"
100%|██████████| 43/43 [02:37<00:00,  3.65s/it]
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HT

EvaluateResponse(
│   generations=[
│   │   {
│   │   │   'generated_answer': "The primary purpose of a W-2 form, also known as a Wage and Tax Statement, is to report an employee's income earned from their employer to the Internal Revenue Service (IRS) for federal income tax purposes. The W-2 form is used by employers to provide employees with a summary of their earnings and taxes withheld from their paychecks throughout the year.\n\nThe W-2 form typically includes information such as:\n\n* Employee's name, address, and Social Security number\n* Employer's name, address, and Employer Identification Number (EIN)\n* Gross wages earned during the tax year\n* Federal income tax withheld\n* State and local taxes withheld (if applicable)\n* Other deductions and credits claimed by the employee\n\nThe primary purpose of a W-2 form is to:\n\n1. Report an employee's income to the IRS: The W-2 form serves as proof of income earned by employees, which is used by the IRS to determine how much tax should be withheld from future paychecks.\n2. Provide information for tax withholding: The W-2 form helps employers calculate and withhold the correct amount of federal income tax, Social Security tax, and Medicare tax from an employee's wages.\n3. Allow employees to file their tax returns accurately: By providing a summary of their earnings and taxes withheld, the W-2 form enables employees to complete their tax returns accurately and claim any additional credits or deductions they may be eligible for.\n\nOverall, the W-2 form plays a critical role in ensuring that employers comply with federal income tax laws and regulations, while also helping employees manage their tax obligations and take advantage of available credits and deductions."
│   │   },
│   │   {
│   │   │   'generated_answer': "As a tax preparer, I'd be happy to explain how W-2 income affects an individual's tax liability.\n\nW-2 income refers to the wages and salaries earned by an employee from their employer. The amount of W-2 income reported on an individual's W-2 form is used to determine their taxable income for the year. Here are some ways in which W-2 income can affect an individual's tax liability:\n\n1. **Taxable Income**: W-2 income is considered taxable income, meaning it is subject to federal and state income taxes. The amount of W-2 income reported on the form will be used to calculate the individual's total taxable income for the year.\n2. **Tax Brackets**: W-2 income falls into one of several tax brackets, which determine the tax rate applied to that income. As an individual earns more W-2 income, they may move up or down a tax bracket, affecting their overall tax liability.\n3. **Deductions and Credits**: Depending on the individual's circumstances, they may be eligible for deductions and credits that can reduce their taxable income. For example, if an individual has health insurance premiums through their employer, they may be able to claim a deduction for those premiums. Similarly, if they have children or are married, they may be eligible for credits like the Earned Income Tax Credit (EITC) or Child Tax Credit.\n4. **Self-Employment Taxes**: If an individual has self-employment income reported on their W-2 form, it will also be subject to self-employment taxes. This can increase their overall tax liability, as self-employment taxes are typically 15.3% of net earnings from self-employment (12.4% for Social Security and 2.9% for Medicare).\n5. **Tax Credits**: Some W-2 income may qualify for tax credits, such as the Child Tax Credit or Education Credits. These credits can directly reduce an individual's tax liability.\n6. **Tax Withholding**: Employers are required to withhold federal income taxes from employee wages and pay them over to the government on behalf of their employees. This withholding reduces the amount of taxes owed when filing a tax return, but it also means that some taxes may be withheld too much, resulting in a larger refund or less tax liability

Now we have the results show that the native Llama3.2 3B instruct model got the avg score of 0.4899 on the tax Q&A eval dataset. Let's see if we can boost the LLM performance with post training.

# 2. Start Post Training
Currenty, Llama stack post training APIs support [Supervised Fine-tune](https://cameronrwolfe.substack.com/p/understanding-and-using-supervised) which is a straightfoard and effective way to boost model performance on specific tasks.

We start from [LoRA finetune algorithm](https://pytorch.org/torchtune/main/tutorials/lora_finetune.html#what-is-lora) that can significantly reduce finetune GPU memory usage as well as needs less data


#### 2.0. Download the base model
Download the Llama model that will be used with [the downloading model CLI](https://llama-stack.readthedocs.io/en/latest/references/llama_cli_reference/download_models.html).

Since ollama takes huggingface safetensor format checkpoint, we need to output the finetuned checkpoint in hugging face format. We download the model checkpoint from huggingface source.

> You need to get a huggingface token from [here](https://huggingface.co/) and replace the "HF_TOKEN"






In [ ]:
!llama download --source huggingface --model-id Llama3.2-3B-Instruct --hf-token "HF_TOKEN"

.gitattributes: 100% 1.52k/1.52k [00:00<00:00, 12.1MB/s]
LICENSE.txt: 100% 7.71k/7.71k [00:00<00:00, 33.3MB/s]
README.md: 100% 41.7k/41.7k [00:00<00:00, 56.9MB/s]
USE_POLICY.md: 100% 6.02k/6.02k [00:00<00:00, 32.4MB/s]
config.json: 100% 878/878 [00:00<00:00, 6.94MB/s]
generation_config.json: 100% 189/189 [00:00<00:00, 1.71MB/s]
model.safetensors.index.json: 100% 20.9k/20.9k [00:00<00:00, 87.0MB/s]
consolidated.00.pth: 100% 6.43G/6.43G [00:18<00:00, 353MB/s]
original%2Forig_params.json: 100% 220/220 [00:00<00:00, 1.69MB/s]
original%2Fparams.json: 100% 220/220 [00:00<00:00, 1.64MB/s]
tokenizer.model: 100% 2.18M/2.18M [00:00<00:00, 44.8MB/s]
special_tokens_map.json: 100% 296/296 [00:00<00:00, 2.69MB/s]
tokenizer.json: 100% 9.09M/9.09M [00:01<00:00, 8.57MB/s]
tokenizer_config.json: 100% 54.5k/54.5k [00:00<00:00, 172MB/s]

Successfully downloaded model to /root/.llama/checkpoints/Llama3.2-3B-Instruct


####  2.1. Prepare post training dataset
Llama stack supports 2 post training dataset formats (instruct and dialog), you can select which dataset format to use in step 2.1.
- instruct dataset:
  - schema:
      - chat_completion_input: string (list of UserMessage, the length of the list is 1)
      - expected_answer: string
  - this format is the abstract of single-turn QA style dataset. During training, tokenized chat_completion_input + expected_answer will be model input, expected_answer will be label to calculate loss
  - [example](https://gist.github.com/SLR722/b4ae7c8b05a0ea1a067e5262eb137ee2)

- dialog dataset
  - schema:
      - dialog: string (list of interleaved UserMessages and AssistantMessages)
  - this format is the abstract of multi-turn chat style dataset. During training, tokenized UserMessage content + AssistantMessage content + UserMessage content + AssistantMessage content ... concat together will be model input, AssistantMessage contents in the list will be label to calculate loss
  - [example](https://gist.github.com/SLR722/20b3929032bc3a94cce3b8cc57788216)


 - Example scripts of converting json format dataset to llama stack format dataset ([to_llama_stack_dataset_instruct.py](https://gist.github.com/SLR722/3a76491190ce3225be935cc63c5332e6), [to_llama_stack_dataset_dialog.py](https://gist.github.com/SLR722/89dd6e41fab4505c327bd3fa99ea2f54))



In our tax preparer example, we prepared a tax Q&A training dataset with synthetic data from Llama 3.3 70B model [tax_preparation_train.csv](https://gist.github.com/SLR722/49a8ce78fc705c0437523d3625c29b5d) (data source: https://github.com/shadi-fsai/modeluniversity/blob/main/trainable_data.json), which has no overlap with eval dataset.

Since the tax Q&A dataset is single round Q&A, we use intruct dataset format for the post training.

> **Note:** if you hit the input schema issue, you probably need to restart the runtime to apply your fix

In [ ]:
import requests

# Upload the example dataset from github to notebook
url = 'https://gist.githubusercontent.com/SLR722/49a8ce78fc705c0437523d3625c29b5d/raw/045f05be9cb6ebd5171fbdfce3306644ee435469/tax_preparation_train.csv'
r = requests.get(url)
with open('tax_preparation_train.csv', 'wb') as f:
    f.write(r.content)

# You can use the below comment out code to upload your local file to the notebook
# from google.colab import files

# uploaded = files.upload()

In [ ]:
import os
import mimetypes
import base64

# encode the dataset file into data_url
def data_url_from_file(file_path: str) -> str:
    if not os.path.exists(file_path):
        raise FileNotFoundError(f"File not found: {file_path}")

    with open(file_path, "rb") as file:
        file_content = file.read()

    base64_content = base64.b64encode(file_content).decode("utf-8")
    mime_type, _ = mimetypes.guess_type(file_path)

    data_url = f"data:{mime_type};base64,{base64_content}"

    return data_url

data_url = data_url_from_file("tax_preparation_train.csv")

# register post training dataset
# use the below commented out version for dialog dataset
response = client.datasets.register(
    purpose="post-training/messages",
    source={
        "type": "uri",
        "uri": data_url,
    },
    dataset_id="post_training_dataset",
)


# response = client.datasets.register(
#     dataset_id="post_training_dataset",
#     provider_id="localfs",
#     url={"uri": data_url},
#     dataset_schema={
#         "dialog": {"type": "dialog"},
#     },
# )

00:42:16.035 [START] /v1/datasets


#### 2.2. Kick-off Post Training Job

You can find the definition of post-training configs and APIs [here for server side](https://github.com/meta-llama/llama-stack/blob/main/llama_stack/apis/post_training/post_training.py) and [here for client side](https://github.com/meta-llama/llama-stack-client-python/blob/d6f3ef24b740c996b29c0540bc6b4e996de0a168/src/llama_stack_client/types/post_training_supervised_fine_tune_params.py).

> **Noet**: If you meet 'Job xxx already exists' error, you may also want to check the error logging above it. Since we have retry logic, the 'Job xxx already exists' may not be the root cause of the job failure

In [ ]:
from llama_stack_client.types.post_training_supervised_fine_tune_params import (
    TrainingConfig,
    TrainingConfigDataConfig,
    TrainingConfigEfficiencyConfig,
    TrainingConfigOptimizerConfig,
)
from llama_stack_client.types.algorithm_config_param import LoraFinetuningConfig
from rich.pretty import pprint

algorithm_config = LoraFinetuningConfig(
    type="LoRA",
    # List of which linear layers LoRA should be applied to in each self-attention block
    # Options are {"q_proj", "k_proj", "v_proj", "output_proj"}.
    lora_attn_modules=["q_proj", "v_proj", "output_proj"],
    # Whether to apply LoRA to the MLP in each transformer layer. Default: False
    apply_lora_to_mlp=True,
    # Whether to apply LoRA to the model's final output projection. Default: False
    apply_lora_to_output=False,
    # Rank of each low-rank approximation
    rank=8,
    # Scaling factor for the low-rank approximation
    alpha=16,
)

data_config = TrainingConfigDataConfig(
    # Identifier of the registered dataset for finetune
    # Use client.datasets.list() to check all the available datasets
    dataset_id="post_training_dataset",
    # Identifier of the registered dataset to validate the finetune model
    # on validation_loss and perplexity
    # Skip this if you don't want to run validatation on the model
    validation_dataset_id="post_training_dataset",
    # Training data batch size
    batch_size=2,
    # Whether to shuffle the dataset.
    shuffle=False,
    # dataset format, select from ['instruct', 'dialog']
    # change it to 'dialog' if you use dialog format dataset
    data_format='instruct',
)
optimizer_config = TrainingConfigOptimizerConfig(
    # Currently only support adamw
    optimizer_type="adamw",
    # Learning rate
    lr=3e-4,
    # adamw weight decay coefficient
    weight_decay=0.1,
    # The number of steps for the warmup phase for lr scheduler
    num_warmup_steps=10,
)
effiency_config = TrainingConfigEfficiencyConfig(
    # Help reduce memory by recalculating some intermediate activations
    # during backward
    enable_activation_checkpointing=True,
    # We offer another memory efficiency flag called enable_activation_offloading
    # which moves certain activations from GPU memory to CPU memory
    # This further reduces GPU memory usage at the cost of additional
    # data transfer overhead and possible slowdowns
    # enable_activation_offloading=False,
)
training_config = TrainingConfig(
    # num of training epochs
    n_epochs=1,
    data_config=data_config,
    efficiency_config=effiency_config,
    optimizer_config=optimizer_config,
    # max num of training steps per epoch
    max_steps_per_epoch=10000,
    # max num of steps for validation
    max_validation_steps=10,
    # Accumulate how many steps to calculate the gradient and update model parameters
    # This is to simulate large batch size training while memory is limited
    gradient_accumulation_steps=4,
)

# call supervised finetune API
training_job = client.post_training.supervised_fine_tune(
    job_uuid="1234",
    # Base Llama model to be finetuned on
    model="meta-llama/Llama-3.2-3B-Instruct",
    algorithm_config=algorithm_config,
    training_config=training_config,
    # Base model checkpoint dir
    # By default, the implementation will look at ~/.llama/checkpoints/<model>
    checkpoint_dir="null",
    # logger_config and hyperparam_search_config haven't been supported yet
    logger_config={},
    hyperparam_search_config={},
)

pprint(training_job)


DEBUG:torchtune.utils._logging:Setting manual seed to local seed 28602197. Local seed is seed + rank = 28602197 + 0
INFO:torchtune.utils._logging:Identified model_type = Llama3_2. Ignoring output.weight in checkpoint in favor of the tok_embedding.weight tied weights.


00:43:22.604 [START] /v1/post-training/supervised-fine-tune


INFO:torchtune.utils._logging:Memory stats after model init:
	GPU peak memory allocation: 6.07 GiB
	GPU peak memory reserved: 6.11 GiB
	GPU peak memory active: 6.07 GiB
INFO:llama_stack.providers.inline.post_training.torchtune.recipes.lora_finetuning_single_device:Model is initialized with precision torch.bfloat16.
INFO:llama_stack.providers.inline.post_training.torchtune.recipes.lora_finetuning_single_device:Tokenizer is initialized.
INFO:llama_stack.providers.inline.post_training.torchtune.recipes.lora_finetuning_single_device:Optimizer is initialized.
INFO:llama_stack.providers.inline.post_training.torchtune.recipes.lora_finetuning_single_device:Loss is initialized.
INFO:llama_stack.providers.inline.post_training.torchtune.recipes.lora_finetuning_single_device:Dataset and Sampler are initialized.
INFO:llama_stack.providers.inline.post_training.torchtune.recipes.lora_finetuning_single_device:Learning rate scheduler is initialized.


Writing logs to /root/.llama/checkpoints/meta-llama/Llama-3.2-3B-Instruct-sft-0/log/log_1740530605.txt


1|1|Loss: 1.389875888824463:   1%|          | 1/153 [00:02<06:02,  2.38s/it]INFO:torchtune.utils._logging:Memory stats after model init:
	GPU peak memory allocation: 6.30 GiB
	GPU peak memory reserved: 6.47 GiB
	GPU peak memory active: 6.30 GiB
1|2|Loss: 1.416195273399353:   1%|▏         | 2/153 [00:03<04:24,  1.75s/it]INFO:torchtune.utils._logging:Memory stats after model init:
	GPU peak memory allocation: 6.35 GiB
	GPU peak memory reserved: 6.47 GiB
	GPU peak memory active: 6.35 GiB
1|3|Loss: 1.5175566673278809:   2%|▏         | 3/153 [00:05<03:54,  1.56s/it]INFO:torchtune.utils._logging:Memory stats after model init:
	GPU peak memory allocation: 6.30 GiB
	GPU peak memory reserved: 6.50 GiB
	GPU peak memory active: 6.30 GiB
1|4|Loss: 1.463149905204773:   3%|▎         | 4/153 [00:06<03:55,  1.58s/it] INFO:torchtune.utils._logging:Memory stats after model init:
	GPU peak memory allocation: 6.33 GiB
	GPU peak memory reserved: 6.50 GiB
	GPU peak memory active: 6.33 GiB
1|5|Loss: 1.500417

PostTrainingJob(job_uuid='1234')

#### 2.3. list all the post training jobs

In [ ]:
job_list = client.post_training.job.list()
pprint(job_list)

00:48:43.629 [START] /v1/post-training/jobs


[Data(job_uuid='1234')]

#### 2.4. query the job status of a given post training job
finetuned checkpoint metadata (validation metrics are included if available) and job metadata are provided in the status

In [ ]:
job_status = client.post_training.job.status(job_uuid='1234')
pprint(job_status)

00:49:06.134 [START] /v1/post-training/job/status


JobStatusResponse(
│   checkpoints=[
│   │   {
│   │   │   'identifier': 'meta-llama/Llama-3.2-3B-Instruct-sft-0',
│   │   │   'created_at': '2025-02-26T00:46:58.602464',
│   │   │   'epoch': 0,
│   │   │   'post_training_job_id': '1234',
│   │   │   'path': '/root/.llama/checkpoints/meta-llama/Llama-3.2-3B-Instruct-sft-0',
│   │   │   'training_metrics': {
│   │   │   │   'epoch': 0,
│   │   │   │   'train_loss': 0.7165011167526245,
│   │   │   │   'validation_loss': 0.3558155596256256,
│   │   │   │   'perplexity': 1.4273443222045898
│   │   │   }
│   │   }
│   ],
│   job_uuid='1234',
│   status='completed',
│   completed_at=datetime.datetime(2025, 2, 26, 0, 47, 4, 901605),
│   resources_allocated={},
│   scheduled_at=datetime.datetime(2025, 2, 26, 0, 43, 22, 601407),
│   started_at=datetime.datetime(2025, 2, 26, 0, 43, 22, 777928)
)

#### 2.5. get list of post training job artifacts (finetuned checkpoints)

In [ ]:
job_artifacts = client.post_training.job.artifacts(job_uuid='1234')
pprint(job_artifacts)

00:49:12.609 [START] /v1/post-training/job/artifacts


JobArtifactsResponse(
│   checkpoints=[
│   │   {
│   │   │   'identifier': 'meta-llama/Llama-3.2-3B-Instruct-sft-0',
│   │   │   'created_at': '2025-02-26T00:46:58.602464',
│   │   │   'epoch': 0,
│   │   │   'post_training_job_id': '1234',
│   │   │   'path': '/root/.llama/checkpoints/meta-llama/Llama-3.2-3B-Instruct-sft-0',
│   │   │   'training_metrics': {
│   │   │   │   'epoch': 0,
│   │   │   │   'train_loss': 0.7165011167526245,
│   │   │   │   'validation_loss': 0.3558155596256256,
│   │   │   │   'perplexity': 1.4273443222045898
│   │   │   }
│   │   }
│   ],
│   job_uuid='1234'
)

# 3. Run Inference on the new model
Woohoo! Now we have the new model finetuned on tax Q&A data ready! Now it's time to run inference to see some response from the model we just made!

#### 3.0. Create a new model on ollama
Please refer to [this doc](https://github.com/ollama/ollama/blob/main/docs/import.md) for more details on how to create a customized model from huggingface safetensor format adapter

We need to launch xterm and enter the below commands


```
mkdir adapter

# copy the adapter checkpoints of the finetuned model from Colab to xterm
cp /root/.llama/checkpoints/meta-llama/Llama-3.2-3B-Instruct-sft-0/adapter/adapter_config.json ./adapter/
cp /root/.llama/checkpoints/meta-llama/Llama-3.2-3B-Instruct-sft-0/adapter/adapter_model.safetensors ./adapter/

# create a Modelfile file
# You need to config the base model in FROM
# and the path of adapter checkpoints in ADAPTER
echo -e "FROM llama3.2\nADAPTER /content/adapter" >> Modelfile

# create the new model
ollama create llama_3_2_finetuned
ollama run llama_3_2_finetuned --keepalive 120m
```

> **TODO**: we plan to streamline this part by managing the finetuned checkpoints across post training and inference provider by /files API and put the above create customized model in ollama part with resigster_model method

In [ ]:
%xterm

Launching Xterm...

<IPython.core.display.Javascript object>

check if the finetuned model is running on ollama server successfully

In [ ]:
!ollama ps

NAME                          ID              SIZE      PROCESSOR    UNTIL            
llama_3_2_finetuned:latest    a73e7ad20955    4.0 GB    100% GPU     2 hours from now    


#### 3.1. Register the new model

In [ ]:
response = client.models.register(
    # the model id here needs to be the finetuned checkpoint identifier
    model_id="meta-llama/Llama-3.2-3B-Instruct-sft-0",
    provider_id="ollama",
    provider_model_id="llama_3_2_finetuned:latest",
    # base model id
    metadata={"llama_model": "meta-llama/Llama-3.2-3B-Instruct"},
)

pprint(response)

INFO:httpx:HTTP Request: GET http://localhost:11434/api/ps "HTTP/1.1 200 OK"


00:53:05.319 [START] /v1/models


Model(
│   identifier='meta-llama/Llama-3.2-3B-Instruct-sft-0',
│   metadata={'llama_model': 'meta-llama/Llama-3.2-3B-Instruct'},
│   api_model_type='llm',
│   provider_id='ollama',
│   provider_resource_id='llama_3_2_finetuned:latest',
│   type='model',
│   model_type='llm'
)

#### 3.2 Call the Llama stack [inference APIs](https://github.com/meta-llama/llama-stack/blob/main/llama_stack/apis/inference/inference.py) to run inference

In [ ]:
response = client.inference.chat_completion(
    model_id="meta-llama/Llama-3.2-3B-Instruct-sft-0",
    messages=[
        {"role": "user", "content": "What is the primary purpose of a W-2 form in relation to income tax?"}
    ],
)

print(response.completion_message.content)

00:53:56.013 [START] /v1/inference/chat-completion


INFO:httpx:HTTP Request: POST http://localhost:11434/api/generate "HTTP/1.1 200 OK"


To report an employee's income and taxes withheld. My explanation: The W-2 form is used by employers to report an employee's income, taxes withheld, and other relevant information to the IRS.


# 4. Run evaluation on the finetuned checkpoints
The finetuned checkpoint is naturally compatiable with Llama stack [eval APIs](https://github.com/meta-llama/llama-stack/blob/main/llama_stack/apis/eval/eval.py).

Let's ru-run the evaluate sub-steps in step 1 to see if the post training gives us some meaningful improvments.

In [ ]:
# We limit to 50 rows from the dataset to save time
eval_rows = client.datasetio.get_rows_paginated(
    dataset_id="eval_dataset",
    limit=-1,
)

from tqdm import tqdm


system_message = {
    "role": "system",
    "content": "You are a tax preparer.",
}

client.benchmarks.register(
    benchmark_id="Llama-3.2-3B-Instruct-sft-0:tax_eval",
    dataset_id="eval_dataset",
    scoring_functions=["braintrust::answer-similarity"]
)

response = client.eval.evaluate_rows(
    benchmark_id="Llama-3.2-3B-Instruct-sft-0:tax_eval",
    input_rows=eval_rows.data,
    scoring_functions=["braintrust::answer-similarity"],
    benchmark_config={
        "type": "benchmark",
        "eval_candidate": {
            "type": "model",
            "model": "meta-llama/Llama-3.2-3B-Instruct-sft-0",
            "sampling_params": {
                "temperature": 0.0,
                "max_tokens": 4096,
                "top_p": 0.9,
                "repeat_penalty": 1.0,
            },
            "system_message": system_message
        }
    }
)
pprint(response)

00:55:41.833 [START] /v1/datasetio/rows
00:55:41.833 [END] /v1/datasetio/rows [StatusCode.OK] (0.21ms)
00:55:41.848 [START] /v1/eval/benchmarks
00:55:41.858 [END] /v1/eval/benchmarks [StatusCode.OK] (9.47ms)
00:55:41.874 [START] /v1/eval/benchmarks/Llama-3.2-3B-Instruct-sft-0:tax_eval/evaluations


100%|██████████| 43/43 [00:25<00:00,  1.68it/s]
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.braintrust.dev/v1/proxy/embeddings "HTTP/1.1 200 OK"
IN

EvaluateResponse(
│   generations=[
│   │   {
│   │   │   'generated_answer': "To report an employee's income and taxes withheld.. My explanation: A W-2 form is used by employers to report an employee's income and taxes withheld, which are then reported on the employee's tax return."
│   │   },
│   │   {
│   │   │   'generated_answer': 'W-2 income is subject to federal and state income taxes, as well as other taxes such as Social Security and Medicare taxes.. My explanation: W-2 income is subject to various taxes, including federal and state income taxes, as well as Social Security and Medicare taxes.'
│   │   },
│   │   {
│   │   │   'generated_answer': 'Yes, W-2 income can be adjusted for tax purposes through various means, such as filing an amended return or claiming a refund.. My explanation: W-2 income can be adjusted for tax purposes through various means, such as filing an amended return or claiming a refund.'
│   │   },
│   │   {
│   │   │   'generated_answer': "Through the Social Security Administration and the Department of Veterans Affairs.. My explanation: The IRS verifies W-2 income through the Social Security Administration and the Department of Veterans Affairs, which can provide information on an individual's earnings history."
│   │   },
│   │   {
│   │   │   'generated_answer': 'W-2 income is reduced by pre-tax deductions, such as health insurance premiums and retirement contributions.. My explanation: Pre-tax deductions reduce W-2 income, which can impact tax liability and benefits eligibility.'
│   │   },
│   │   {
│   │   │   'generated_answer': 'Yes, if an employee has multiple jobs or is self-employed.. My explanation: If an individual has multiple jobs or is self-employed, they may have multiple W-2 forms to report their income and taxes withheld.'
│   │   },
│   │   {
│   │   │   'generated_answer': 'Tax credits can reduce W-2 income, which in turn reduces taxable income.. My explanation: Tax credits can reduce W-2 income, which in turn reduces taxable income and lowers the amount of taxes owed.'
│   │   },
│   │   {
│   │   │   'generated_answer': 'W-2 income can trigger AMT if it exceeds certain thresholds.. My explanation: W-2 income can trigger the Alternative Minimum Tax (AMT) if it exceeds certain thresholds, which can result in additional tax liability.'
│   │   },
│   │   {
│   │   │   'generated_answer': 'The TCJA reduced the top marginal tax rate from 39.6% to 37%. My explanation: The TCJA made significant changes to the tax code, including reducing the top marginal tax rate from 39.6% to 37%, which affects W-2 income.'
│   │   },
│   │   {
│   │   │   'generated_answer': 'W-2 income is subject to NIIT, which can increase the overall tax liability.. My explanation: W-2 income is subject to NIIT, which can increase the overall tax liability.'
│   │   },
│   │   {
│   │   │   'generated_answer': 'The ACA requires employers to provide health insurance coverage to employees, which can impact W-2 income.. My explanation: The ACA has changed the way employers report W-2 income, as they must now include information about health insurance coverage.'
│   │   },
│   │   {
│   │   │   'generated_answer': 'Self-Employment Tax is calculated based on net earnings from self-employment, which includes W-2 income.. My explanation: Self-Employment Tax is calculated based on net earnings from self-employment, which includes W-2 income.'
│   │   },
│   │   {
│   │   │   'generated_answer': 'It is excluded from US taxable income, but may be subject to withholding and reporting requirements.. My explanation: The Foreign Earned Income Exclusion allows certain foreign earned income to be excluded from US taxable income. However, it may still be subject to withholding and reporting requirements.'
│   │   },
│   │   {
│   │   │   'generated_answer': 'Self-employment income, rent, and royalty income.. My explanation: Self-employment income, rent, and royalty income are typically reported on a 1099-MISC form.'
│   │   }

Wow, you see? we are able to improve the eval score from 0.4899 to 0.5803 (**18.5% improvement**) with a ~1000 samples dataset and a few mintutes training on a single GPU!


It's just a start. There are several tricks on parameters tuning, training dataset processing etc. to further boost the finetune performance for you to explore.

Now, it's time to enhance your own agentic application with post training. Happy tuning!